### 1. 크롤링 df, 행민 df 통합하기 = 최종 df 생성
#### -> 이용되는 df는 총 5개: 
1. 최종 df (크롤링 데이터로 행민 누락 데이터 보충 -> 3번을 만들기 위한 용도)
2. 전화번호 df (전화번호 룰베이스로 뽑는 용도)
3. faiss 벡터db + 메타데이터 df (RAG 이용 용도)
4. 사무명 + 질문 + 답변 df (임베딩 모델 파인튜닝, LLM 모델 파인튜닝 용도)
5. 다산콜센터 일반행정 문의 데이터 (테스트 용도) https://aihub.or.kr/aihubdata/data/view.do?dataSetSn=98

In [2]:
print('hello')

hello


In [22]:
import pandas as pd

# 긴 열 생략 없이 전체 표시
pd.set_option('display.max_colwidth', None)

# 전체 열 표시 (생략 방지)
pd.set_option('display.max_columns', None)

# 행 생략 방지 (원한다면)
pd.set_option('display.max_rows', None)

In [23]:
df1 = pd.read_excel("행정안전부_민원안내정보_20250327.xlsx")

df1.info()
df1.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6022 entries, 0 to 6021
Data columns (total 15 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   분류번호    6022 non-null   object
 1   사무명     6022 non-null   object
 2   사무개요    6022 non-null   object
 3   신청유형    6022 non-null   object
 4   신청자 자격  6020 non-null   object
 5   수수료     6021 non-null   object
 6   수수료내역   6018 non-null   object
 7   소관부처    6022 non-null   object
 8   담당부서    6022 non-null   object
 9   접수방법    6022 non-null   object
 10  접수/처리   6013 non-null   object
 11  근거법령    5981 non-null   object
 12  신청서     5124 non-null   object
 13  발급물 내용  918 non-null    object
 14  구비서류    5372 non-null   object
dtypes: object(15)
memory usage: 705.8+ KB


분류번호               사무명  \
0  SG4CADM-2015   토지임야대장등본교부 다량신청   
1  9740000-0009  공탁신청(공탁물지급청구 포함)   
2  9740000-0008         친양자입양취소신고   
3  9740000-0007           친양자파양신고   
4  9740000-0006         성·본계속사용신고   

                                                                                                                                                                                                                                                      사무개요  \
0                                                                                                                                                                                                            토지임야대장등본교부 민원에 대하여 여러 번지를 한번에 신청할 수 있는 민원입니다.   
1  공탁 신청, 공탁금의 지급을 위한 민원입니다. 공탁은 공탁자가 법령에 규정된 원인에 따라 금전, 유가증권, 그 밖의 물품을 공탁소에 맡기고, 일정한 자가 수령하도록 함으로써 채무의 변제, 손해의 담보, 집행목적물의 관리 및 집행당사자에의 교부, 목적물의 보관 등의 목적을 달성하게 하는 제도입니다. ※ 공탁의 종류에 따라 공탁신청시 또는 지급청구시 신청서와 첨부서류가 다르므로, 구체적인 첨부서류 등은 해당 공탁소로 문의하여 주시기 바랍니다.   
2                                                                                                                                                                                                                 가정법원의 허가를 얻어 친양자 입양을 취소하기 위해 신청하는 민원입니다.   
3                                                                                                                                                                            가정법원의 허가를 얻어 친양자입양을 파양하고자 하는 사람이 재판의 확정일부터 1개월 이내에 가족관계등록 관서의 장에게 신고하는 민원입니다.   
4                                                                                                                                                                                  부가 혼인외 자를 인지할 때 인지 전의 자녀의 성과 본을 유지할 경우 그 취지를 가족관계등록 관서의 장에게 신고하는 민원입니다.   

  신청유형   신청자 자격     수수료   수수료내역   소관부처     담당부서     접수방법  \
0   교부  누구나신청가능     NaN     NaN  국토교통부  공간정보제도과      인터넷   
1   승인  누구나신청가능  수수료 없음  수수료 없음    대법원    사법등기국  방문, 인터넷   
2   신고  누구나신청가능  수수료 없음  수수료 없음    대법원  가족관계등록과   방문, 우편   
3   신고  누구나신청가능  수수료 없음  수수료 없음    대법원  가족관계등록과   방문, 우편   
4   신고  누구나신청가능  수수료 없음  수수료 없음    대법원  가족관계등록과   방문, 우편   

                                                            접수/처리  \
0                                                             NaN   
1     1. 유형없음(총 0일)\n*접수:지방법원.지원(0일)\n*경유:\n*협의:\n*처리:지방법원.지원(0일)   
2      1. 유형없음( 즉시)\n*접수:시.구.읍.면(0일)\n*경유:\n*협의:\n*처리:시.구.읍.면(즉시)   
3  1. 유형없음( 지체없이)\n*접수:시.구.읍.면(0일)\n*경유:\n*협의:\n*처리:시.구.읍.면(지체없이)   
4     1. 유형없음(총 0일)\n*접수:시.구.읍.면(0일)\n*경유:\n*협의:\n*처리:시.구.읍.면(0일)   

                                                                                                               근거법령  \
0                                                                                                               NaN   
1  1. 공탁법(제4조, 제9조) \n2. 공탁규칙(제20조, 제21조, 제23조, 제24조, 제32조, 제33조, 제34조, 제37조, 제38조) \n3. 공탁사무 문서양식에 관한 예규(제1조, 제2조)   
2                                                                                  1. 가족관계의 등록 등에 관한 법률(제69조, 제70조)   
3                                                                                        1. 가족관계의 등록 등에 관한 법률(제69조)   
4                                                                                    1. 가족관계의 등록 등에 관한 법률(제55조 제1항)   

                                           신청서 발급물 내용  \
0                                          NaN    NaN   
1  금전공탁서(변제 등) 공탁사무 문서양식에 관한 예규 : 별지서식 1호의 1\n    NaN   
2                           제9호, 친양자 입양취소신고서\n    NaN   
3                              제7호, 친양자파양신고서\n    NaN   
4                            제3호, 성·본계속사용신고서\n    NaN   

                                                                                                                                                                                                                                                                                                                                                                          구비서류  
0                                                           

In [24]:
#0번째 row 누락데이터 채워넣기


In [25]:
# "지문등 사전등록 신청"이 포함된 행만 필터링
result = df1[df1['사무명'].str.contains("지문등 사전등록 신청", na=False)]

# 결과 출력
result.head()

분류번호          사무명  \
4581  1320000-0052  지문등 사전등록 신청   

                                                                                      사무개요  \
4581  실종아동등의 예방 및 조속한 발견과 복귀를 위하여 아동등의 보호자가 신청하는 경우 아동등의 지문 및 얼굴 등에 관한 정보를 미리 등록하는 민원사무입니다   

     신청유형            신청자 자격     수수료   수수료내역 소관부처    담당부서  \
4581   등록  법령상의자격이있는 자(제3자)  수수료 없음  수수료 없음  경찰청  청소년보호과   

                                      접수방법  \
4581  방문, 우편, 전화, FAX, 인터넷, 모바일, 현장제출 및 기타   

                                                         접수/처리  \
4581  1. 유형없음(총 0일)\n*접수:경찰서, 파출소(0일)\n*경유:\n*협의:\n*처리:경찰서(0일)   

                                                                              근거법령  \
4581  1. 실종아동등의 보호 및 지원에 관한 법률(제7조의2 제1항) \n2. 실종아동등의 발견 및 유전자검사 등에 관한 규칙(제3조 제2항)   

                                                     신청서 발급물 내용  \
4581  아동등 사전등록신청서 실종아동등의 발견 및 유전자검사 등에 관한 규칙 : 별지서식 1호\n    NaN   

                                                                                              구비서류  
4581  1. 유형없음\n< 공무원확인사항 >\n(1) 주민등록표 등본\n(2) 장애인증명서 (등록대상 아동등이 지적장애인, 자폐성장애인 또는 정신장애인인 경우만 해당합니다)

In [26]:
import pandas as pd

# 크롤링 데이터
df2 = pd.read_csv("full_df2.csv", encoding="utf-8-sig")
df2.info()
df2.head()  # 데이터 일부 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10263 entries, 0 to 10262
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   URL     10263 non-null  object
 1   제목      10252 non-null  object
 2   내용      10263 non-null  object
dtypes: object(3)
memory usage: 240.7+ KB


URL  \
0    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03004&CappBizCD=15701000076&tp_seq=   
1  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000052&tp_seq=01   
2    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12100000169&tp_seq=   
3  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A02002&CappBizCD=14800000063&tp_seq=01   
4                                   https://www.gov.kr/portal/service/serviceInfo/403000000147   

                                 제목  \
0                               NaN   
1                       지문등 사전등록 신청   
2  교통·에너지·환경세 미납세(면세) 반출물품 멸실승인(신청)   
3           특정토양오염관리대상시설 설치변경(폐쇄)신고   
4                     노인 버스 무료승차 지원   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  내용  
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        알 수 없는 레이아웃  
1  서비스 개요신청방법인터넷,방문,FAX,우편,모바일,전화,현장제출 및 기타신청자격법령상의 자격이 있는  자(제3자)처리기간즉시(근무시간 내 3시간)처리기간 계산 방법신청서아동등 사전등록신청서 (실종아동등의 발견 및 유전자검사 등에 관한 규칙 : 별지서식 1호)신청작성예시구비서류구비서류 없음수수료수수료 없음기본정보제공 내용이 민원은 실종아동등의 예방 및 조속한 발견과 복귀를 위하여 아동등의 보호자가 신청하는 경우 아동등의 지문 및 얼굴 등에 관한 정보를 미리 등록하는 민원사무입니다신청시기제한없음후속 조치사항- 경찰청에서는 사전등록 신청에 따라 등록된 지문등정보를 데이터베이스로 구축, 운영할 수 있습니다.- 누구든지 정당한 사유 없이 지문등정보를 실종아동등을 찾기 위한 목적 외로 이용하여서는 아니되며, 이를 위반하여 지문등정보를 실종아동등을 찾기 위한 목적 외로 이용한 경우 2년 이하의 징역 또는 1천만원 이하의 벌금에 처합니다.신청자격아동등의 보호자신청 방법 및 절차1접수경찰서파출소2처리경찰서참고각 기관을 선택하면 해당기관 정보조회가 가능하며, 조회된 접수/처리기관에 대한 실제 민원 접수/처리 가능여부는 해당기관에 확인해 주시기 바랍니다.제출 서류민원인이 제출해야하는 서류없음민원인이 제출하지 않아도 되는 서류 (담당공무원이 확인)주민등록표 등본장애인증명서 (등록대상 아동등이 지적장애인, 자폐성장애인 또는 정신장애인인 경우만 해당합니다)참고담당공무원 확인, 본인정보 제공 요구 사항은 본인이 행정정보공동이용에 동의하지 않는 경우 민원인

In [27]:
#0번째 row 누락데이터 채워넣기
df2.at[0, '제목'] = "정보통신기술자(인정,등급변경,경력인정, 전자형변경)신청"
df2.at[0, '내용'] = "서비스 개요신청방법방문신청자격누구나 신청 가능처리기간총 7일처리기간 계산 방법신청서정보통신기술자(인정,등급변경,경력인정, 전자형 변경) 신청서 (정보통신공사업법 시행에 관한 규정 : 별지서식 30호)구비서류있음 (하단 참조)수수료정보통신공사업법 제57조제1항 관련 수수료기본정보제공 내용이 민원은 정보통신공사업법 제39조 및 같은 법 시행령 제39조에 따라 정보통신기술자로 인정받고자 하는 자가 해당 서류(자격증 등)을 구비하여 위탁기관인 한국정보통신공사협회에 신청신청 방법 및 절차1접수한국정보통신공사협회2처리한국정보통신공사협회참고각 기관을 선택하면 해당기관 정보조회가 가능하며, 조회된 접수/처리기관에 대한 실제 민원 접수/처리 가능여부는 해당기관에 확인해 주시기 바랍니다.제출 서류민원인이 제출해야하는 서류사진(2.5cm*3cm) 2매(등급변경은 1매)별지 제2호서식의 경력확인서(재직사실을 증명하는 서류가 첨부된 경우에 한함)정보통신기술자 경력수첩(등급변경 및 경력인정에 한함)신분증 원본 제시민원인이 제출하지 않아도 되는 서류 (담당공무원이 확인)외국인등록사실증명, 병적증명서, 건강보험자격득실확인서, 국민연금가입자가입증명, 국가기술자격취득사항확인서고등학교졸업증명서참고담당공무원 확인, 본인정보 제공 요구 사항은 본인이 행정정보공동이용에 동의하지 않는 경우 민원인이 제출하여야 합니다.부가정보근거법령정보통신공사업법 (제39조) (제69조 제2항 제4호) (제73조 제6호)정보통신공사업법 시행령 (제39조) (제53조 제2항 제5호) (제57조 제1항)정보통신공사업법 시행에 관한 규정 (제11조 [별지 제30호 서식])제도를 담당하는 기관 :과학기술정보통신부네트워크정책과위 담당부서와 전화번호는 이 민원의 제도를 담당하고 있는 (중앙)행정기관입니다.개별 민원에 대한 문의 사항은 접수·처리기관(관할처리기관)과 연락하시기 바랍니다.정보 변경 내역최근 내용 변경일 : 2024-11-11최근 내용 확인일 : 2024-11-11"

df2.head(20)

URL  \
0     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03004&CappBizCD=15701000076&tp_seq=   
1   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000052&tp_seq=01   
2     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12100000169&tp_seq=   
3   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A02002&CappBizCD=14800000063&tp_seq=01   
4                                    https://www.gov.kr/portal/service/serviceInfo/403000000147   
5   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03007&CappBizCD=15200000480&tp_seq=01   
6   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=14100000069&tp_seq=01   
7   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12200000235&tp_seq=01   
8                                    https://www.gov.kr/portal/service/serviceInfo/508000000565   
9                                    https://www.gov.kr/portal/service/serviceInfo/356000000232   
10                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050340   
11                                   https://www.gov.kr/portal/service/serviceInfo/SME000000100   
12    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09006&CappBizCD=14500000023&tp_seq=   
13    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09008&CappBizCD=13800000270&tp_seq=   
14                                   https://www.gov.kr/portal/service/serviceInfo/B19000100012   
15                                   https://www.gov.kr/portal/service/serviceInfo/PTR000052608   
16                                   https://www.gov.kr/portal/service/serviceInfo/B19002400015   
17    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=13500000078&tp_seq=   
18  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A05001&CappBizCD=14600000250&tp_seq=01   
19                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050573   

                                  제목  \
0     정보통신기술자(인정,등급변경,경력인정, 전자형변경)신청   
1                        지문등 사전등록 신청   
2   교통·에너지·환경세 미납세(면세) 반출물품 멸실승인(신청)   
3            특정토양오염관리대상시설 설치변경(폐쇄)신고   
4                      노인 버스 무료승차 지원   
5                       선원취업규칙(변경)신고   
6                    도시가스 비상공급시설설치신고   
7                     용도세율 전용물품 승인신청   
8             자립준비청년(보호종료아동) 자립수당 지급   
9                 청라복합문화센터 수영장 이용 지원   
10                    4대 사회보험료 미납내역서   
11                       난임부부 시술비 지원   
12                합성천연가스제조업 허가(변경허가)   
13                 품종보호 등에 대한 가등록 신청   
14            수의계약 정보 열람 서비스(한국조폐공사)   
15                      도로굴착 온라인 시스템   
16                      손실보상 절차 및 기준   
17                 방사성폐기물 자체처분계획서 신고   
18           정신요양시설 설치허가 및 허가사항 변경통지   
19                     임대 주택 불법거래 신고   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [28]:
#크롤링 데이터 사무 개요 column 생성
import re

def extract_summary(text):
    if not isinstance(text, str):
        return None
    # "제공 내용이 민원은 " 다음부터 "신청 방법" 또는 "신청시기" 전까지 추출
    match = re.search(r"제공 내용이 민원은 (.*?)(신청 방법|신청시기)", text)
    if match:
        return match.group(1).strip()
    return None

# "사무 개요" 컬럼 생성
df2['사무 개요'] = df2['내용'].apply(extract_summary)

df2.head()

URL  \
0    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03004&CappBizCD=15701000076&tp_seq=   
1  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000052&tp_seq=01   
2    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12100000169&tp_seq=   
3  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A02002&CappBizCD=14800000063&tp_seq=01   
4                                   https://www.gov.kr/portal/service/serviceInfo/403000000147   

                                 제목  \
0    정보통신기술자(인정,등급변경,경력인정, 전자형변경)신청   
1                       지문등 사전등록 신청   
2  교통·에너지·환경세 미납세(면세) 반출물품 멸실승인(신청)   
3           특정토양오염관리대상시설 설치변경(폐쇄)신고   
4                     노인 버스 무료승차 지원   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  내용  \
0                                                                                                                                                                                                                                                                                         서비스 개요신청방법방문신청자격누구나 신청 가능처리기간총 7일처리기간 계산 방법신청서정보통신기술자(인정,등급변경,경력인정, 전자형 변경) 신청서 (정보통신공사업법 시행에 관한 규정 : 별지서식 30호)구비서류있음 (하단 참조)수수료정보통신공사업법 제57조제1항 관련 수수료기본정보제공 내용이 민원은 정보통신공사업법 제39조 및 같은 법 시행령 제39조에 따라 정보통신기술자로 인정받고자 하는 자가 해당 서류(자격증 등)을 구비하여 위탁기관인 한국정보통신공사협회에 신청신청 방법 및 절차1접수한국정보통신공사협회2처리한국정보통신공사협회참고각 기관을 선택하면 해당기관 정보조회가 가능하며, 조회된 접수/처리기관에 대한 실제 민원 접수/처리 가능여부는 해당기관에 확인해 주시기 바랍니다.제출 서류민원인이 제출해야하는 서류사진(2.5cm*3cm) 2매(등급변경은 1매)별지 제2호서식의 경력확인서(재직사실을 증명하는 서류가 첨부된 경우에 한함)정보통신기술자 경력수첩(등급변경 및 경력인정에 한함)신분증 원본 제시민원인이 제출하지 않아도 되는 서류 (담당공무원이 확인)외국인등록사실증명, 병적증명서, 건강보험자격득실확인서, 국민연금가입자가입증명, 국가기술자격취득사항확인서고등학교졸업증명서참고담당공무원 확인, 본인정보 제공 요구 사항은 본인이 행정정보공동이용에 동의하지 않는 경우 민원인이 제출하여야 합니다.부가정보근거법령정보통신공사업법 (제39조) (제69조 제2항 제4호) (제73조 제6호)정보통신공사업법 시행령 (제39조) (제53조 제2항 제5호) (제57조 제1항)정보통신공사업법 시행에 관한 규정 (제11조 [별지 제30호 서식])제도를 담당하는 기관 :과학기술정보통신부네트워크정책과위 담당부서와 전화번호는 이 민원의 제도를 담당하고 있는 (중앙)행정기관입니다.개별 민원에 대한 문의 사항은 접수·처리기관(관할처리기관)과 연락하시기 바랍니다.정보 변경 내역최근 내용 변경일 : 2024-11-11최근 내용 확인일 : 2024-11-11   
1  서비스 개요신청방법인터넷,방문,FAX,우편,모바일,전화,현장제출 및 기타신청자격법령상의 자격이 있는  자(제3자)처리기간즉시(근무시간 내 3시간)처리기간 계산 방법신청서아동등 사전등록신청서 (실종아동등의 발견 및 유전자검사 등에 관한 규칙 : 별지서식 1호)신청작성예시구비서류구비서류 없음수수료수수료 없음기본정보제공 내용이 민원은 실종아동등의 예방 및 조속한 발견과 복귀를 위하여 아동등의 보호자가 신청하는 경우 아동등의 지문 및 얼굴 등에 관한 정보를 미리 등록하는 민원사무입니다신청시기제한없음후속 조치사항- 경찰청에서는 사전등록 신청에 따라 등록된 지문등정보를 데이터베이스로 구축, 운영할 수 있습니다.- 누구든지 정당한 사유 없이 지문등정보를 실종아동등을 찾기 위한 목적 외로 이용하여서는 아니되며, 이를 위반하여 지문등정보를 실종아동등을 찾기 위한 목적 외로 이용한 경우 2년 이하의 징역 또는 1천만원 이하의 벌금에 처합니다.신청자격아동등의 보호자신청 방법 및 절차1접수경찰서파출소2처리경찰서참고각 기관을 선택하면 해당기관 정보조회가 가능하며, 조회된 접수/처리기관에 대한 실제 민원 접수/처리 가능여부는 해당기관에 확인해 주시기 바랍니다.제출 서류민원인이 제출해야하는 서류없음민원인이 제출하지 않아도 되는 서류 (담당공무원이 확인)주민등록표 등본장애인증명서 (등록대상 아동등이 지적장애인, 자폐성장애인 또는 정신장애인인 경우만 해당합니다)참고담당공무원 확인, 본인정보 제공 요구 사항은 본인이 행정정보공동이용에 동의하지 않는 경우 민

In [29]:
# "제공 내용이 민원은 " 텍스트만 삭제
df2['내용'] = df2['내용'].str.replace("제공 내용이 민원은 ", "", regex=False)

df2.head(20)

URL  \
0     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03004&CappBizCD=15701000076&tp_seq=   
1   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000052&tp_seq=01   
2     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12100000169&tp_seq=   
3   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A02002&CappBizCD=14800000063&tp_seq=01   
4                                    https://www.gov.kr/portal/service/serviceInfo/403000000147   
5   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03007&CappBizCD=15200000480&tp_seq=01   
6   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=14100000069&tp_seq=01   
7   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12200000235&tp_seq=01   
8                                    https://www.gov.kr/portal/service/serviceInfo/508000000565   
9                                    https://www.gov.kr/portal/service/serviceInfo/356000000232   
10                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050340   
11                                   https://www.gov.kr/portal/service/serviceInfo/SME000000100   
12    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09006&CappBizCD=14500000023&tp_seq=   
13    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09008&CappBizCD=13800000270&tp_seq=   
14                                   https://www.gov.kr/portal/service/serviceInfo/B19000100012   
15                                   https://www.gov.kr/portal/service/serviceInfo/PTR000052608   
16                                   https://www.gov.kr/portal/service/serviceInfo/B19002400015   
17    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=13500000078&tp_seq=   
18  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A05001&CappBizCD=14600000250&tp_seq=01   
19                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050573   

                                  제목  \
0     정보통신기술자(인정,등급변경,경력인정, 전자형변경)신청   
1                        지문등 사전등록 신청   
2   교통·에너지·환경세 미납세(면세) 반출물품 멸실승인(신청)   
3            특정토양오염관리대상시설 설치변경(폐쇄)신고   
4                      노인 버스 무료승차 지원   
5                       선원취업규칙(변경)신고   
6                    도시가스 비상공급시설설치신고   
7                     용도세율 전용물품 승인신청   
8             자립준비청년(보호종료아동) 자립수당 지급   
9                 청라복합문화센터 수영장 이용 지원   
10                    4대 사회보험료 미납내역서   
11                       난임부부 시술비 지원   
12                합성천연가스제조업 허가(변경허가)   
13                 품종보호 등에 대한 가등록 신청   
14            수의계약 정보 열람 서비스(한국조폐공사)   
15                      도로굴착 온라인 시스템   
16                      손실보상 절차 및 기준   
17                 방사성폐기물 자체처분계획서 신고   
18           정신요양시설 설치허가 및 허가사항 변경통지   
19                     임대 주택 불법거래 신고   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [31]:
# 이미 사무 개요가 있는 row의 인덱스를 저장할 리스트
already_has_summary = []

# "사이트 가기어떤 내용인지 궁금하시죠?" 이전 텍스트를 사무 개요로 이동
for idx, row in df2.iterrows():
    content = row['내용']
    if isinstance(content, str) and "사이트 가기어떤 내용인지 궁금하시죠?" in content:
        summary = content.split("사이트 가기어떤 내용인지 궁금하시죠?")[0]
        # 이미 사무 개요가 있으면 인덱스 저장
        if pd.notnull(row.get('사무 개요')) and str(row['사무 개요']).strip() != '':
            already_has_summary.append(idx)
        else:
            df2.at[idx, '사무 개요'] = summary.strip()

# 이미 사무 개요가 있던 row 번호 출력
print("이미 사무 개요가 있던 row 번호:", already_has_summary)

이미 사무 개요가 있던 row 번호: []


In [32]:
df2.head(20)

URL  \
0     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03004&CappBizCD=15701000076&tp_seq=   
1   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000052&tp_seq=01   
2     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12100000169&tp_seq=   
3   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A02002&CappBizCD=14800000063&tp_seq=01   
4                                    https://www.gov.kr/portal/service/serviceInfo/403000000147   
5   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03007&CappBizCD=15200000480&tp_seq=01   
6   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=14100000069&tp_seq=01   
7   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12200000235&tp_seq=01   
8                                    https://www.gov.kr/portal/service/serviceInfo/508000000565   
9                                    https://www.gov.kr/portal/service/serviceInfo/356000000232   
10                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050340   
11                                   https://www.gov.kr/portal/service/serviceInfo/SME000000100   
12    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09006&CappBizCD=14500000023&tp_seq=   
13    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09008&CappBizCD=13800000270&tp_seq=   
14                                   https://www.gov.kr/portal/service/serviceInfo/B19000100012   
15                                   https://www.gov.kr/portal/service/serviceInfo/PTR000052608   
16                                   https://www.gov.kr/portal/service/serviceInfo/B19002400015   
17    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=13500000078&tp_seq=   
18  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A05001&CappBizCD=14600000250&tp_seq=01   
19                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050573   

                                  제목  \
0     정보통신기술자(인정,등급변경,경력인정, 전자형변경)신청   
1                        지문등 사전등록 신청   
2   교통·에너지·환경세 미납세(면세) 반출물품 멸실승인(신청)   
3            특정토양오염관리대상시설 설치변경(폐쇄)신고   
4                      노인 버스 무료승차 지원   
5                       선원취업규칙(변경)신고   
6                    도시가스 비상공급시설설치신고   
7                     용도세율 전용물품 승인신청   
8             자립준비청년(보호종료아동) 자립수당 지급   
9                 청라복합문화센터 수영장 이용 지원   
10                    4대 사회보험료 미납내역서   
11                       난임부부 시술비 지원   
12                합성천연가스제조업 허가(변경허가)   
13                 품종보호 등에 대한 가등록 신청   
14            수의계약 정보 열람 서비스(한국조폐공사)   
15                      도로굴착 온라인 시스템   
16                      손실보상 절차 및 기준   
17                 방사성폐기물 자체처분계획서 신고   
18           정신요양시설 설치허가 및 허가사항 변경통지   
19                     임대 주택 불법거래 신고   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [33]:
def remove_before_and_including(text, keyword):
    if isinstance(text, str) and keyword in text:
        return text.split(keyword, 1)[1]
    return text

df2['내용'] = df2['내용'].apply(lambda x: remove_before_and_including(x, "사이트 가기어떤 내용인지 궁금하시죠?"))
df2.head(20)

URL  \
0     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03004&CappBizCD=15701000076&tp_seq=   
1   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000052&tp_seq=01   
2     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12100000169&tp_seq=   
3   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A02002&CappBizCD=14800000063&tp_seq=01   
4                                    https://www.gov.kr/portal/service/serviceInfo/403000000147   
5   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03007&CappBizCD=15200000480&tp_seq=01   
6   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=14100000069&tp_seq=01   
7   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12200000235&tp_seq=01   
8                                    https://www.gov.kr/portal/service/serviceInfo/508000000565   
9                                    https://www.gov.kr/portal/service/serviceInfo/356000000232   
10                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050340   
11                                   https://www.gov.kr/portal/service/serviceInfo/SME000000100   
12    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09006&CappBizCD=14500000023&tp_seq=   
13    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09008&CappBizCD=13800000270&tp_seq=   
14                                   https://www.gov.kr/portal/service/serviceInfo/B19000100012   
15                                   https://www.gov.kr/portal/service/serviceInfo/PTR000052608   
16                                   https://www.gov.kr/portal/service/serviceInfo/B19002400015   
17    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=13500000078&tp_seq=   
18  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A05001&CappBizCD=14600000250&tp_seq=01   
19                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050573   

                                  제목  \
0     정보통신기술자(인정,등급변경,경력인정, 전자형변경)신청   
1                        지문등 사전등록 신청   
2   교통·에너지·환경세 미납세(면세) 반출물품 멸실승인(신청)   
3            특정토양오염관리대상시설 설치변경(폐쇄)신고   
4                      노인 버스 무료승차 지원   
5                       선원취업규칙(변경)신고   
6                    도시가스 비상공급시설설치신고   
7                     용도세율 전용물품 승인신청   
8             자립준비청년(보호종료아동) 자립수당 지급   
9                 청라복합문화센터 수영장 이용 지원   
10                    4대 사회보험료 미납내역서   
11                       난임부부 시술비 지원   
12                합성천연가스제조업 허가(변경허가)   
13                 품종보호 등에 대한 가등록 신청   
14            수의계약 정보 열람 서비스(한국조폐공사)   
15                      도로굴착 온라인 시스템   
16                      손실보상 절차 및 기준   
17                 방사성폐기물 자체처분계획서 신고   
18           정신요양시설 설치허가 및 허가사항 변경통지   
19                     임대 주택 불법거래 신고   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [34]:
# 이미 사무 개요가 있는 row의 인덱스를 저장할 리스트
already_has_summary = []

# "어떤 내용인지 궁금하시죠?" 이전 텍스트를 사무 개요로 이동
for idx, row in df2.iterrows():
    content = row['내용']
    if isinstance(content, str) and "어떤 내용인지 궁금하시죠?" in content:
        summary = content.split("어떤 내용인지 궁금하시죠?")[0]
        # 이미 사무 개요가 있으면 인덱스 저장
        if pd.notnull(row.get('사무 개요')) and str(row['사무 개요']).strip() != '':
            already_has_summary.append(idx)
        else:
            df2.at[idx, '사무 개요'] = summary.strip()

# 이미 사무 개요가 있던 row 번호 출력
print("이미 사무 개요가 있던 row 번호:", already_has_summary)

이미 사무 개요가 있던 row 번호: []


In [35]:
df2.head(20)

URL  \
0     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03004&CappBizCD=15701000076&tp_seq=   
1   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000052&tp_seq=01   
2     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12100000169&tp_seq=   
3   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A02002&CappBizCD=14800000063&tp_seq=01   
4                                    https://www.gov.kr/portal/service/serviceInfo/403000000147   
5   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03007&CappBizCD=15200000480&tp_seq=01   
6   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=14100000069&tp_seq=01   
7   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12200000235&tp_seq=01   
8                                    https://www.gov.kr/portal/service/serviceInfo/508000000565   
9                                    https://www.gov.kr/portal/service/serviceInfo/356000000232   
10                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050340   
11                                   https://www.gov.kr/portal/service/serviceInfo/SME000000100   
12    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09006&CappBizCD=14500000023&tp_seq=   
13    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09008&CappBizCD=13800000270&tp_seq=   
14                                   https://www.gov.kr/portal/service/serviceInfo/B19000100012   
15                                   https://www.gov.kr/portal/service/serviceInfo/PTR000052608   
16                                   https://www.gov.kr/portal/service/serviceInfo/B19002400015   
17    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=13500000078&tp_seq=   
18  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A05001&CappBizCD=14600000250&tp_seq=01   
19                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050573   

                                  제목  \
0     정보통신기술자(인정,등급변경,경력인정, 전자형변경)신청   
1                        지문등 사전등록 신청   
2   교통·에너지·환경세 미납세(면세) 반출물품 멸실승인(신청)   
3            특정토양오염관리대상시설 설치변경(폐쇄)신고   
4                      노인 버스 무료승차 지원   
5                       선원취업규칙(변경)신고   
6                    도시가스 비상공급시설설치신고   
7                     용도세율 전용물품 승인신청   
8             자립준비청년(보호종료아동) 자립수당 지급   
9                 청라복합문화센터 수영장 이용 지원   
10                    4대 사회보험료 미납내역서   
11                       난임부부 시술비 지원   
12                합성천연가스제조업 허가(변경허가)   
13                 품종보호 등에 대한 가등록 신청   
14            수의계약 정보 열람 서비스(한국조폐공사)   
15                      도로굴착 온라인 시스템   
16                      손실보상 절차 및 기준   
17                 방사성폐기물 자체처분계획서 신고   
18           정신요양시설 설치허가 및 허가사항 변경통지   
19                     임대 주택 불법거래 신고   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [36]:
def remove_before_and_including(text, keyword):
    if isinstance(text, str) and keyword in text:
        return text.split(keyword, 1)[1]
    return text

df2['내용'] = df2['내용'].apply(lambda x: remove_before_and_including(x, "어떤 내용인지 궁금하시죠?"))

df2.head(20)

URL  \
0     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03004&CappBizCD=15701000076&tp_seq=   
1   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000052&tp_seq=01   
2     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12100000169&tp_seq=   
3   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A02002&CappBizCD=14800000063&tp_seq=01   
4                                    https://www.gov.kr/portal/service/serviceInfo/403000000147   
5   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03007&CappBizCD=15200000480&tp_seq=01   
6   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=14100000069&tp_seq=01   
7   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09002&CappBizCD=12200000235&tp_seq=01   
8                                    https://www.gov.kr/portal/service/serviceInfo/508000000565   
9                                    https://www.gov.kr/portal/service/serviceInfo/356000000232   
10                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050340   
11                                   https://www.gov.kr/portal/service/serviceInfo/SME000000100   
12    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09006&CappBizCD=14500000023&tp_seq=   
13    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09008&CappBizCD=13800000270&tp_seq=   
14                                   https://www.gov.kr/portal/service/serviceInfo/B19000100012   
15                                   https://www.gov.kr/portal/service/serviceInfo/PTR000052608   
16                                   https://www.gov.kr/portal/service/serviceInfo/B19002400015   
17    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=13500000078&tp_seq=   
18  https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A05001&CappBizCD=14600000250&tp_seq=01   
19                                   https://www.gov.kr/portal/service/serviceInfo/PTR000050573   

                                  제목  \
0     정보통신기술자(인정,등급변경,경력인정, 전자형변경)신청   
1                        지문등 사전등록 신청   
2   교통·에너지·환경세 미납세(면세) 반출물품 멸실승인(신청)   
3            특정토양오염관리대상시설 설치변경(폐쇄)신고   
4                      노인 버스 무료승차 지원   
5                       선원취업규칙(변경)신고   
6                    도시가스 비상공급시설설치신고   
7                     용도세율 전용물품 승인신청   
8             자립준비청년(보호종료아동) 자립수당 지급   
9                 청라복합문화센터 수영장 이용 지원   
10                    4대 사회보험료 미납내역서   
11                       난임부부 시술비 지원   
12                합성천연가스제조업 허가(변경허가)   
13                 품종보호 등에 대한 가등록 신청   
14            수의계약 정보 열람 서비스(한국조폐공사)   
15                      도로굴착 온라인 시스템   
16                      손실보상 절차 및 기준   
17                 방사성폐기물 자체처분계획서 신고   
18           정신요양시설 설치허가 및 허가사항 변경통지   
19                     임대 주택 불법거래 신고   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [37]:
# NaN 또는 빈 문자열("")인 경우 모두 포함
empty_count = df2['사무 개요'].isna().sum() + (df2['사무 개요'] == '').sum()
print("사무 개요에 내용이 없는 row 개수:", empty_count)

사무 개요에 내용이 없는 row 개수: 915


In [41]:
# 사무 개요가 NaN이거나, 공백/빈 문자열인 row만 필터링
filtered_df = df2[df2['사무 개요'].apply(lambda x: pd.isna(x) or str(x).strip() == '')]

# 결과 DataFrame 확인
filtered_df.head(40)

URL  \
4                                     https://www.gov.kr/portal/service/serviceInfo/403000000147   
26                                    https://www.gov.kr/portal/service/serviceInfo/305000000165   
30                                    https://www.gov.kr/portal/service/serviceInfo/494000000161   
33                                    https://www.gov.kr/portal/service/serviceInfo/515000000153   
37                                    https://www.gov.kr/portal/service/serviceInfo/554000000173   
42     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=14100000071&tp_seq=   
49   https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09005&CappBizCD=15000000378&tp_seq=01   
55                                    https://www.gov.kr/portal/service/serviceInfo/476000000154   
77                                    https://www.gov.kr/portal/service/serviceInfo/300000000141   
82                                    https://www.gov.kr/portal/service/serviceInfo/499000000152   
93                                    https://www.gov.kr/portal/service/serviceInfo/875000000020   
103                                   https://www.gov.kr/portal/service/serviceInfo/641000000189   
105                                   https://www.gov.kr/portal/service/serviceInfo/383000000139   
116                                   https://www.gov.kr/portal/service/serviceInfo/447000000134   
118                                   https://www.gov.kr/portal/service/serviceInfo/650000000332   
146                                   https://www.gov.kr/portal/service/serviceInfo/476000000166   
157                                   https://www.gov.kr/portal/service/serviceInfo/378000000167   
181                                   https://www.gov.kr/portal/service/serviceInfo/461000000142   
197                                   https://www.gov.kr/portal/service/serviceInfo/450000000146   
208                                   https://www.gov.kr/portal/service/serviceInfo/305000000137   
215                                   https://www.gov.kr/portal/service/serviceInfo/393000000150   
244                                   https://www.gov.kr/portal/service/serviceInfo/B01000300011   
256                                   https://www.gov.kr/portal/service/serviceInfo/399000000117   
302                                   https://www.gov.kr/portal/service/serviceInfo/515000000133   
307                                   https://www.gov.kr/portal/service/serviceInfo/641000000192   
326                                   https://www.gov.kr/portal/service/serviceInfo/650000000331   
328                                   https://www.gov.kr/portal/service/serviceInfo/554000000134   
330                                   https://www.gov.kr/portal/service/serviceInfo/304000000197   
331    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A08003&CappBizCD=13200000076&tp_seq=   
339        https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=&CappBizCD=14800000110&tp_seq=01   
341                                   https://www.gov.kr/portal/service/serviceInfo/476000000161   
346                                   https://www.gov.kr/portal/service/serviceInfo/307000000120   
359                                   https://www.gov.kr/portal/service/serviceInfo/515000000144   
365                                   https://www.gov.kr/portal/service/serviceInfo/402000000123   
375                                   https://www.gov.kr/portal/service/serviceInfo/305000000155   
379                                   https://www.gov.kr/portal/service/serviceInfo/403000000145   
386                                   https://www.gov.kr/portal/service/serviceInfo/505000000132   
392                                   https://www.gov.kr/portal/service/serviceInfo/348000000428   
415    https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09006&CappBizCD=14110000048&tp_seq=   
419                                   https://www.gov.kr/portal/service/serviceInfo/383000000

In [45]:
import os
from dotenv import load_dotenv
from openai import OpenAI
import time
import pandas as pd

# .env 파일에서 환경변수 불러오기
load_dotenv()
client = OpenAI(api_key=os.getenv("OPENAI_API_KEY"))

# gpt-4o-mini 가격 (2025년 5월 기준)
input_price_per_1k = 0.00015
output_price_per_1k = 0.0006

total_input_tokens = 0
total_output_tokens = 0

def get_summary(row):
    global total_input_tokens, total_output_tokens
    prompt = f"""{row['내용']}

해당 글에서 지원하는 내용을 간략하게 한 줄로 요약해줘. 대상, 지원 내용(금액이 있으면 금액 포함) 등.
"""
    try:
        response = client.chat.completions.create(
            model="gpt-4o-mini",
            messages=[
                {"role": "system", "content": "당신은 행정서비스 요약 전문가입니다."},
                {"role": "user", "content": prompt}
            ],
            max_tokens=100,
            temperature=0.2
        )
        summary = response.choices[0].message.content.strip()
        usage = response.usage
        total_input_tokens += usage.prompt_tokens
        total_output_tokens += usage.completion_tokens
        return summary
    except Exception as e:
        print(f"Error at row {row.name}: {e}")
        return None

# 제목이 비어있지 않은 row만 GPT 작업 진행
for idx, row in filtered_df.iterrows():
    if pd.isna(row['제목']) or str(row['제목']).strip() == '':
        continue  # 제목이 없으면 건너뜀
    summary = get_summary(row)
    filtered_df.at[idx, '사무 개요'] = summary
    time.sleep(1)  # 요청 간 1초 대기 (rate limit 방지)

# 비용 계산
input_cost = (total_input_tokens / 1000) * input_price_per_1k
output_cost = (total_output_tokens / 1000) * output_price_per_1k
total_cost = input_cost + output_cost

print(f"총 입력 토큰: {total_input_tokens}")
print(f"총 출력 토큰: {total_output_tokens}")
print(f"예상 총 비용: ${total_cost:.6f} (입력: ${input_cost:.6f}, 출력: ${output_cost:.6f})")

# 결과 확인 (필요시)
print(filtered_df[['URL', '제목', '내용', '사무 개요']])

총 입력 토큰: 464192
총 출력 토큰: 48057
예상 총 비용: $0.098463 (입력: $0.069629, 출력: $0.028834)
                                                                                               URL  \
4                                       https://www.gov.kr/portal/service/serviceInfo/403000000147   
26                                      https://www.gov.kr/portal/service/serviceInfo/305000000165   
30                                      https://www.gov.kr/portal/service/serviceInfo/494000000161   
33                                      https://www.gov.kr/portal/service/serviceInfo/515000000153   
37                                      https://www.gov.kr/portal/service/serviceInfo/554000000173   
42       https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A03006&CappBizCD=14100000071&tp_seq=   
49     https://www.gov.kr/mw/AA020InfoCappView.do?HighCtgCD=A09005&CappBizCD=15000000378&tp_seq=01   
55                                      https://www.gov.kr/portal/service/serviceInfo/476000000154   
7

In [30]:
# df1의 '사무명'과 df2의 '제목' 비교
s1 = df1['사무명']
s2 = df2['제목']

# df1 기준: df2에 없는 사무명
not_in_df2 = s1[~s1.isin(s2)].reset_index(drop=True)

# df2 기준: df1에 없는 제목
not_in_df1 = s2[~s2.isin(s1)].reset_index(drop=True)

print('df1에는 있지만 df2에는 없는 사무명:')
print(not_in_df2)

print('\ndf2에는 있지만 df1에는 없는 제목:')
print(not_in_df1)

df1에는 있지만 df2에는 없는 사무명:
0                                                                    건물등기사항증명서 발급
1                                                                    토지등기사항증명서 발급
2                                                                    법인등기사항증명서 발급
3                                                      천연기념물 · 명승의 소재지(보관장소) 변경신고
4                                                           천연기념물 · 명승의 소유자등 변경신고
5                                                      천연기념물 · 명승의 멸실·유실·도난·훼손 신고
6                                                       천연기념물 · 명승의 관리자 선임(해임) 신고
7                                                       천연기념물 · 명승 공개 제한지역 출입허가신청
8                                                                천연기념물 국외 반출 허가신청
9                                                          천연기념물 국외 반출 기간 연장 허가신청
10                                                                 천연기념물 국내 반입 신고
11                                                         자연유산 조사 등으로 인한 

### 2. 파인튜닝 임베딩 모델로 생성한 벡터db VS 기본 임베딩 모델로 생성한 벡터db
#### -> 주제 발표 때 나온 질문에 대한 방어: RAG 성능 비교 필요

### 3. 파이프라인 구조 계획 확실하게 (문서화 -> 추후 보고서에 이용 + 코드 구현)

In [60]:
import os
from dotenv import load_dotenv
from openai import OpenAI
import time
import re

# .env 파일에서 환경변수 불러오기
load_dotenv()

# OpenAI 클라이언트 초기화
client = OpenAI(api_key=os.getenv("OPENAI_API_KEY"))

def check_confirmation_status(messages):
    """
    대화 기록을 분석하여 다음 조건을 모두 만족하는지 판단:
    1. 챗봇이 확인 질문("이게 맞아?", "맞을까요?" 등)을 했는가?
    2. 사용자가 그 직후에 짧은 긍정 대답("응 맞아", "네" 등)을 했는가?
    
    Returns:
        0: 위 조건을 만족하지 않음 (기존 모델 계속 사용)
        1: 위 조건을 모두 만족함 (다음 단계로 진행)
    """
    try:
        # 최소 2개의 메시지가 있어야 함 (챗봇 확인 질문 + 사용자 답변)
        if len(messages) < 2:
            return 0
            
        # 마지막 2개 메시지 확인 (챗봇 질문 -> 사용자 답변)
        last_bot_message = None
        last_user_message = None
        
        # 뒤에서부터 찾기
        for i in range(len(messages) - 1, -1, -1):
            if messages[i]['role'] == 'user' and last_user_message is None:
                last_user_message = messages[i]['content']
            elif messages[i]['role'] == 'assistant' and last_user_message is not None and last_bot_message is None:
                last_bot_message = messages[i]['content']
                break
        
        if not last_bot_message or not last_user_message:
            return 0
        
        response = client.chat.completions.create(
            model="gpt-4o-mini",
            messages=[
                {"role": "system", "content": "당신은 대화 분석 전문가입니다. 주어진 챗봇의 마지막 메시지와 사용자의 마지막 응답을 분석하여 다음 조건을 모두 만족하는지 판단하세요:\n\n1. 챗봇이 사용자에게 확인을 요청하는 질문을 했는가? (예: '맞을까요?', '이게 맞아?', '확인해 주세요' 등)\n2. 사용자가 그에 대해 짧고 명확한 긍정적 답변을 했는가? (예: '네', '맞아요', '응 맞아', '맞습니다' 등)\n\n두 조건을 모두 만족하면 '1'을, 그렇지 않으면 '0'을 출력하세요. 오직 숫자만 출력하세요."},
                {"role": "user", "content": f"챗봇의 마지막 메시지: {last_bot_message}\n\n사용자의 마지막 응답: {last_user_message}"}
            ],
            max_tokens=5,  # 0 또는 1만 출력하면 되므로 매우 짧게 설정
            temperature=0.1  # 일관성을 위해 낮은 temperature
        )
        
        result = response.choices[0].message.content.strip()
        
        # 결과가 0 또는 1인지 확인하고 정수로 변환
        if result in ['0', '1']:
            return int(result)
        else:
            # 예상치 못한 응답의 경우 기본적으로 0 (계속 진행)
            print(f"예상치 못한 응답: {result}, 기본값 0 반환")
            return 0
            
    except Exception as e:
        print(f"확인 상태 판단 중 오류: {e}")
        return 0  # 오류 시 기본적으로 0 반환

def summarize_conversation(messages):
    """
    전체 대화 내역에서 핵심 단어들을 조합한 의미있는 구문으로 요약하는 함수
    
    Args:
        messages: 전체 대화 기록 리스트
        
    Returns:
        str: 핵심 단어들로 조합된 간결한 구문
    """
    try:
        # 시스템 메시지를 제외한 사용자-챗봇 대화만 추출
        conversation_text = ""
        for msg in messages[1:]:  # 첫 번째는 시스템 메시지이므로 제외
            if msg['role'] == 'user':
                conversation_text += f"사용자: {msg['content']}\n"
            elif msg['role'] == 'assistant':
                conversation_text += f"챗봇: {msg['content']}\n"
        
        response = client.chat.completions.create(
            model="gpt-4o-mini",
            messages=[
                {"role": "system", "content": "당신은 민원 요약 전문가입니다. 주어진 대화에서 사용자의 요청사항을 **핵심 단어들을 조합한 간결한 구문**으로 요약하세요.\n\n**요약 규칙:**\n1. 핵심 단어들을 의미있게 조합하여 하나의 구문을 만드세요\n2. 2-4개의 단어로 구성된 간결한 구문으로 작성하세요\n3. 명사+명사, 명사+동사, 형용사+명사 등의 조합을 활용하세요\n4. 불필요한 조사나 어미는 제거하세요\n5. 관공서 업무와 관련된 구문으로 작성하세요\n\n**예시:**\n- 입력: 고양이가 아파서 보호소에 연락하고 싶어요\n- 출력: 동물보호소 연락\n\n- 입력: 친자확인을 받고 싶어요\n- 출력: 친자확인 문의\n\n- 입력: 전입신고를 하려고 해요\n- 출력: 전입신고 접수\n\n간결하고 명확한 구문만 출력하세요."},
                {"role": "user", "content": f"다음 대화에서 핵심 구문을 추출해주세요:\n\n{conversation_text}"}
            ],
            max_tokens=50,  # 구문 출력을 위해 약간 늘림
            temperature=0.1   # 일관성을 위해 낮은 temperature
        )
        
        summary = response.choices[0].message.content.strip()
        return summary
        
    except Exception as e:
        print(f"요약 생성 중 오류: {e}")
        return "요약 생성 실패"

# 대화 기록을 저장할 리스트 초기화
messages = [
    {"role": "system", "content": "당신은 관공서 민원 챗봇입니다. 민원인이 정확히 무엇을 원하는지 파악하는 것이 임무입니다.\n\n**응답 규칙:**\n1. 한 번에 질문은 반드시 하나만 하세요.\n2. 질문은 짧고 간결하게 하세요.\n3. 여러 질문을 동시에 하지 마세요.\n4. 간단명료한 언어를 사용하세요.\n5. 요청이 파악되면 간단히 요약하고 '맞을까요?'로 확인하세요.\n6. 직접적인 답변이나 해결책은 제공하지 마세요.\n\n**예시:**\n- 좋음: '어떤 종류의 문제인가요?'\n- 나쁨: '어떤 종류의 문제인가요? 언제 발생했나요? 어디에서 일어났나요?'\n\n항상 한국어로 응답하세요."},
]

print("저는 관공서 챗봇 관공이입니다. 무엇을 도와드릴까요?")
print("(종료하려면 'quit' 또는 'exit' 입력)")

# 대화 루프
while True:
    # 사용자 입력 받기
    user_input = input("나: ")

    # 사용자 입력 출력
    print(f"나: {user_input}")

    # 종료 조건 확인
    if user_input.lower() in ['quit', 'exit']:
        print("대화를 종료합니다.")
        break

    # 사용자 메시지를 대화 기록에 추가
    messages.append({"role": "user", "content": user_input})

    # LLM을 통해 다음 단계로 넘어가도 되는지 확인
    confirmation_status = check_confirmation_status(messages)
    
    if confirmation_status == 1:
        # 챗봇이 확인 질문했고 사용자가 짧은 긍정 답변함 - 다음 단계로 진행
        print("챗봇: 요청이 확인되었습니다. 다음 단계로 진행합니다.")
        
        # 요약 LLM 호출하여 핵심 구문 추출
        print("\n--- 요약 진행 중 ---")
        summary_phrase = summarize_conversation(messages)
        print(f"핵심 구문: {summary_phrase}")
        
        # TODO: 이후 추출된 구문을 활용한 추가 처리 로직
        # 예: RAG 시스템에 구문 전달, 관련 문서 검색 등
        
        break  # 대화 종료
        
    else:
        # 아직 확인 조건을 만족하지 않음 - 기존 모델 계속 사용
        try:
            response = client.chat.completions.create(
                model="gpt-4o-mini",
                messages=messages,
                max_tokens=200,  # 짧은 응답을 위해 토큰 수 줄임
                temperature=0.2
            )

            assistant_response = response.choices[0].message.content
            print(f"챗봇: {assistant_response}")

            # 모델 응답을 대화 기록에 추가
            messages.append({"role": "assistant", "content": assistant_response})

            time.sleep(0.5)

        except Exception as e:
            print(f"API 호출 중 오류 발생: {e}")
            break

저는 관공서 챗봇 관공이입니다. 무엇을 도와드릴까요?
(종료하려면 'quit' 또는 'exit' 입력)
나: 안녕
챗봇: 안녕하세요! 어떤 도움이 필요하신가요?
나: 아들을 파양하고 싶어 절차가 어떻게 돼?
챗봇: 아들을 파양하고 싶으신가요? 관련된 절차에 대해 알고 싶으신 건가요?
나: 응
챗봇: 아들을 파양하는 절차에 대해 알고 싶으신 것이군요. 맞을까요?
나: 응
챗봇: 요청이 확인되었습니다. 다음 단계로 진행합니다.

--- 요약 진행 중 ---
핵심 구문: 아들 파양 절차


### 4. 이후 스트림릿 .py 로 서비스 시각화 하기 (프로토타입 만들기)